**Hagan una copia de este notebook y comincen a ejecutar las ventanas.**

In [283]:
import sqlite3
import pandas as pd

conn = sqlite3.connect(':memory:')

create_statements = [
'''
create table classroom
	(building		varchar(15),
	 room_number		varchar(7),
	 capacity		numeric(4,0),
	 primary key (building, room_number)
	);

''',
'''
create table department
	(dept_name		varchar(20),
	 building		varchar(15),
	 budget		        numeric(12,2) check (budget > 0),
	 primary key (dept_name)
	);

''',
'''
create table course
	(course_id		varchar(8),
	 title			varchar(50),
	 dept_name		varchar(20),
	 credits		numeric(2,0) check (credits > 0),
	 primary key (course_id),
	 foreign key (dept_name) references department
		on delete set null
	);

''',
'''
create table instructor
	(ID			varchar(5),
	 name			varchar(20) not null,
	 dept_name		varchar(20),
	 salary			numeric(8,2) check (salary > 29000),
	 primary key (ID),
	 foreign key (dept_name) references department
		on delete set null
	);
''',
'''
create table section
	(course_id		varchar(8),
         sec_id			varchar(8),
	 semester		varchar(6)
		check (semester in ('Fall', 'Winter', 'Spring', 'Summer')),
	 year			numeric(4,0) check (year > 1701 and year < 2100),
	 building		varchar(15),
	 room_number		varchar(7),
	 time_slot_id		varchar(4),
	 primary key (course_id, sec_id, semester, year),
	 foreign key (course_id) references course
		on delete cascade,
	 foreign key (building, room_number) references classroom
		on delete set null
	);

''',
'''
create table teaches
	(ID			varchar(5),
	 course_id		varchar(8),
	 sec_id			varchar(8),
	 semester		varchar(6),
	 year			numeric(4,0),
	 primary key (ID, course_id, sec_id, semester, year),
	 foreign key (course_id,sec_id, semester, year) references section
		on delete cascade,
	 foreign key (ID) references instructor
		on delete cascade
	);

''',
'''
create table student
	(ID			varchar(5),
	 name			varchar(20) not null,
	 dept_name		varchar(20),
	 tot_cred		numeric(3,0) check (tot_cred >= 0),
	 primary key (ID),
	 foreign key (dept_name) references department
		on delete set null
	);

''',
'''
create table takes
	(ID			varchar(5),
	 course_id		varchar(8),
	 sec_id			varchar(8),
	 semester		varchar(6),
	 year			numeric(4,0),
	 grade		        varchar(2),
	 primary key (ID, course_id, sec_id, semester, year),
	 foreign key (course_id,sec_id, semester, year) references section
		on delete cascade,
	 foreign key (ID) references student
		on delete cascade
	);

''',
'''
create table advisor
	(s_ID			varchar(5),
	 i_ID			varchar(5),
	 primary key (s_ID),
	 foreign key (i_ID) references instructor (ID)
		on delete set null,
	 foreign key (s_ID) references student (ID)
		on delete cascade
	);

''',
'''
create table time_slot
	(time_slot_id		varchar(4),
	 day			varchar(1),
	 start_hr		numeric(2) check (start_hr >= 0 and start_hr < 24),
	 start_min		numeric(2) check (start_min >= 0 and start_min < 60),
	 end_hr			numeric(2) check (end_hr >= 0 and end_hr < 24),
	 end_min		numeric(2) check (end_min >= 0 and end_min < 60),
	 primary key (time_slot_id, day, start_hr, start_min)
	);

''',
'''
create table prereq
	(course_id		varchar(8),
	 prereq_id		varchar(8),
	 primary key (course_id, prereq_id),
	 foreign key (course_id) references course
		on delete cascade,
	 foreign key (prereq_id) references course
	);
'''
]

for create_statement in create_statements:
    conn.execute(create_statement)


In [284]:
query = "SELECT * FROM sqlite_master WHERE type='table';"
# query = "SELECT * FROM sqlite_master WHERE 1;"
result = pd.read_sql_query(query, conn)
print(result)

     type        name    tbl_name  rootpage  \
0   table   classroom   classroom         2   
1   table  department  department         4   
2   table      course      course         6   
3   table  instructor  instructor         8   
4   table     section     section        10   
5   table     teaches     teaches        12   
6   table     student     student        14   
7   table       takes       takes        16   
8   table     advisor     advisor        18   
9   table   time_slot   time_slot        20   
10  table      prereq      prereq        22   

                                                  sql  
0   CREATE TABLE classroom\n\t(building\t\tvarchar...  
1   CREATE TABLE department\n\t(dept_name\t\tvarch...  
2   CREATE TABLE course\n\t(course_id\t\tvarchar(8...  
3   CREATE TABLE instructor\n\t(ID\t\t\tvarchar(5)...  
4   CREATE TABLE section\n\t(course_id\t\tvarchar(...  
5   CREATE TABLE teaches\n\t(ID\t\t\tvarchar(5),\n...  
6   CREATE TABLE student\n\t(ID\t\t\tvarcha

In [285]:
query = "SELECT * FROM classroom WHERE 1;"
result = pd.read_sql_query(query, conn)
print(result)

Empty DataFrame
Columns: [building, room_number, capacity]
Index: []


In [286]:

classroom_data = [('Science Bldg', '101', 60),
('Liberal Arts', '201', 30),
('Engineering', '301', 40)]

conn.executemany('INSERT INTO classroom VALUES (?, ?, ?);', classroom_data)


In [287]:
query = "SELECT * from classroom;"
result = pd.read_sql_query(query, conn)
result

building room_number  capacity
0  Science Bldg         101        60
1  Liberal Arts         201        30
2   Engineering         301        40

In [288]:
query = "delete from classroom;"
conn.execute(query)


In [289]:
ClassroomData = [('ZL7101', '011', 66), ('Yb5300', '597', 24), ('lT9721', '108', 10), ('De7318', '918', 21), ('eP9048', '475', 84)]
DepartmentData = [('Physics', 'Qb3378', 2711.38), ('Computer Science', 'TE1052', 34961.28), ('Mathematics', 'Fk2019', 5822.68), ('Biology', 'wX8320', 18377.14)]
CourseData = [('rjtj402', 'American history glass.', 'Physics', 3), ('EcYE597', 'Think keep sit spring.', 'Biology', 4), ('XlAB441', 'Voice billion.', 'Biology', 4), ('Pmwg764', 'Oil wall.', 'Computer Science', 1), ('Uefz257', 'Answer experience.', 'Computer Science', 1), ('fYSu038', 'War at.', 'Physics', 4), ('mgzm416', 'May stand guess.', 'Computer Science', 1), ('lLnt386', 'Spend move.', 'Biology', 4), ('viid787', 'Close certain national research.', 'Physics', 1), ('OfWY200', 'Trip always.', 'Biology', 1)]
InstructorData = [('65364', 'Tammy Henderson', 'Mathematics', 87706.72), ('92814', 'James Cunningham', 'Physics', 75124.4), ('81643', 'Russell Sanders', 'Biology', 89512.49), ('57372', 'Aaron Castillo', 'Mathematics', 47440.65), ('46726', 'Brooke Vargas', 'Computer Science', 61737.16)]
SectionData = [('viid787', '95', 'Fall', 2016, 'ZL7101', '011', 'nkH'), ('fYSu038', '97', 'Winter', 2022, 'De7318', '918', 'ZQE'), ('XlAB441', '07', 'Fall', 2002, 'eP9048', '918', 'QZg'), ('XlAB441', '05', 'Fall', 2017, 'Yb5300', '597', 'YEe'), ('rjtj402', '29', 'Spring', 2024, 'ZL7101', '475', 'vwW'), ('XlAB441', '44', 'Spring', 2014, 'ZL7101', '918', 'RRL'), ('Uefz257', '59', 'Fall', 2005, 'lT9721', '597', 'sKm'), ('Uefz257', '84', 'Winter', 2024, 'De7318', '011', 'eIS'), ('OfWY200', '93', 'Summer', 2024, 'lT9721', '918', 'vGv'), ('fYSu038', '57', 'Summer', 2015, 'ZL7101', '918', 'rfW')]
StudentData = [('89981', 'Dawn Taylor', 'Biology', 43), ('06003', 'Wanda Black', 'Biology', 132), ('68144', 'Susan Robinson', 'Biology', 75), ('81095', 'Crystal Woods', 'Mathematics', 31), ('28991', 'Travis Sanchez', 'Computer Science', 106), ('28865', 'Zachary Knight', 'Biology', 30), ('99705', 'Jacob Pittman', 'Biology', 26), ('60991', 'Marcus Gonzalez', 'Biology', 96), ('86970', 'Robert Clayton', 'Mathematics', 49), ('65273', 'Rebecca Lin', 'Mathematics', 27)]
TakesData =  [('81095', 'Uefz257', '84', 'Winter', 2024, 'D'), ('99705', 'XlAB441', '07', 'Fall', 2002, 'C'), ('06003', 'viid787', '95', 'Fall', 2016, 'D'), ('28991', 'Uefz257', '59', 'Fall', 2005, 'D'), ('86970', 'Uefz257', '84', 'Winter', 2024, 'D'), ('68144', 'Uefz257', '84', 'Winter', 2024, 'C'), ('28865', 'fYSu038', '57', 'Summer', 2015, 'I'), ('86970', 'fYSu038', '57', 'Summer', 2015, 'B'), ('86970', 'XlAB441', '07', 'Fall', 2002, 'F'), ('60991', 'Uefz257', '84', 'Winter', 2024, 'I')]
AdvisorData = [('89981', '65364'), ('68144', '92814'), ('99705', '81643'), ('81095', '57372')]
TimeSlotData = [('wLx', 'Su', 8, 34, 20, 58), ('Ale', 'W', 13, 20, 21, 36), ('Obn', 'Su', 4, 53, 17, 5), ('XmM', 'Su', 8, 17, 13, 25), ('NJU', 'Su', 18, 17, 16, 7)]
PrereqData = [('rjtj402', 'lLnt386'), ('rjtj402', 'fYSu038'), ('XlAB441', 'lLnt386'), ('Uefz257', 'viid787'), ('mgzm416', 'XlAB441'), ('lLnt386', 'Uefz257')]
TeachesData =  [('57372', 'viid787', '95', 'Fall', 2016), ('57372', 'fYSu038', '97', 'Winter', 2022), ('81643', 'XlAB441', '07', 'Fall', 2002), ('57372', 'XlAB441', '05', 'Fall', 2017), ('57372', 'rjtj402', '29', 'Spring', 2024), ('92814', 'XlAB441', '44', 'Spring', 2014), ('57372', 'Uefz257', '59', 'Fall', 2005), ('57372', 'Uefz257', '84', 'Winter', 2024), ('92814', 'OfWY200', '93', 'Summer', 2024), ('92814', 'fYSu038', '57', 'Summer', 2015)]


In [290]:
conn.executemany('INSERT INTO classroom VALUES (?, ?, ?);', ClassroomData)
conn.executemany('INSERT INTO department VALUES (?, ?, ?);', DepartmentData)
conn.executemany('INSERT INTO course VALUES (?, ?, ?, ?);', CourseData)
conn.executemany('INSERT INTO instructor VALUES (?, ?, ?, ?);', InstructorData)
conn.executemany('INSERT INTO section VALUES (?, ?, ?, ?, ?, ?, ?);', SectionData)
conn.executemany('INSERT INTO student VALUES (?, ?, ?, ?);', StudentData)
conn.executemany('INSERT INTO takes VALUES (?, ?, ?,?, ?, ?);', TakesData)
conn.executemany('INSERT INTO advisor VALUES (?, ?);', AdvisorData)
conn.executemany('INSERT INTO time_slot VALUES (?, ?, ?, ?, ?, ?);', TimeSlotData)
conn.executemany('INSERT INTO prereq VALUES (?, ?);', PrereqData)
conn.executemany('INSERT INTO teaches VALUES (?, ?, ?, ?, ?);', TeachesData)


In [255]:
SectionData

[('viid787', '95', 'Fall', 2016, 'ZL7101', '011', 'nkH'),
 ('fYSu038', '97', 'Winter', 2022, 'De7318', '918', 'ZQE'),
 ('XlAB441', '07', 'Fall', 2002, 'eP9048', '918', 'QZg'),
 ('XlAB441', '05', 'Fall', 2017, 'Yb5300', '597', 'YEe'),
 ('rjtj402', '29', 'Spring', 2024, 'ZL7101', '475', 'vwW'),
 ('XlAB441', '44', 'Spring', 2014, 'ZL7101', '918', 'RRL'),
 ('Uefz257', '59', 'Fall', 2005, 'lT9721', '597', 'sKm'),
 ('Uefz257', '84', 'Winter', 2024, 'De7318', '011', 'eIS'),
 ('OfWY200', '93', 'Summer', 2024, 'lT9721', '918', 'vGv'),
 ('fYSu038', '57', 'Summer', 2015, 'ZL7101', '918', 'rfW')]

In [256]:
query = "SELECT * from section;"
result = pd.read_sql_query(query, conn)
result

course_id sec_id semester  year building room_number time_slot_id
0   viid787     95     Fall  2016   ZL7101         011          nkH
1   fYSu038     97   Winter  2022   De7318         918          ZQE
2   XlAB441     07     Fall  2002   eP9048         918          QZg
3   XlAB441     05     Fall  2017   Yb5300         597          YEe
4   rjtj402     29   Spring  2024   ZL7101         475          vwW
5   XlAB441     44   Spring  2014   ZL7101         918          RRL
6   Uefz257     59     Fall  2005   lT9721         597          sKm
7   Uefz257     84   Winter  2024   De7318         011          eIS
8   OfWY200     93   Summer  2024   lT9721         918          vGv
9   fYSu038     57   Summer  2015   ZL7101         918          rfW

In [257]:
query = "SELECT * from takes;"
result = pd.read_sql_query(query, conn)
result

ID course_id sec_id semester  year grade
0  81095   Uefz257     84   Winter  2024     D
1  99705   XlAB441     07     Fall  2002     C
2  06003   viid787     95     Fall  2016     D
3  28991   Uefz257     59     Fall  2005     D
4  86970   Uefz257     84   Winter  2024     D
5  68144   Uefz257     84   Winter  2024     C
6  28865   fYSu038     57   Summer  2015     I
7  86970   fYSu038     57   Summer  2015     B
8  86970   XlAB441     07     Fall  2002     F
9  60991   Uefz257     84   Winter  2024     I

In [258]:
# conn.close()


#### Ejercicios:

1. Encuentra los nombres de todos los instructores.
2. Lista todos los cursos con menos de 3 créditos.
3. Muestra los nombres de los estudiantes junto con los nombres de los departamentos a los que pertenecen.
4. Calcula el salario promedio de los instructores en el departamento de 'Computer Science'.
5. Encuentra el número de estudiantes inscritos en cada departamento.
6. Muestra los nombres de los estudiantes y los títulos de los cursos que están tomando este semestre.
7. Lista estudiantes que toman o han tomado clases en el edificio "ZL7101"
8. Lista los cursos que tienen más estudiantes inscritos que el promedio de inscripciones de todos los cursos.
9. Encuentra los instructores que enseñan más de un curso, incluyendo los títulos de los cursos que enseñan.
10. Entra datos para que la pregunta 6 no salga vacía.

#### Instrucciones:
- Utiliza el esquema de base de datos proporcionado para realizar cada uno de los ejercicios.
- Verifica tus resultados ejecutando las consultas.
- Intenta resolver los ejercicios en orden, ya que están diseñados para aumentar gradualmente en dificultad.

1. Encuentra los nombres de todos los instructores.


In [259]:
query = "SELECT name from instructor;"
result = pd.read_sql_query(query, conn)
result

name
0   Tammy Henderson
1  James Cunningham
2   Russell Sanders
3    Aaron Castillo
4     Brooke Vargas

2. Lista todos los cursos con menos de 3 créditos.

In [260]:
query = '''
SELECT * from course
where course.credits <3 ;
'''
result = pd.read_sql_query(query, conn)
result

course_id                             title         dept_name  credits
0   Pmwg764                         Oil wall.  Computer Science        1
1   Uefz257                Answer experience.  Computer Science        1
2   mgzm416                  May stand guess.  Computer Science        1
3   viid787  Close certain national research.           Physics        1
4   OfWY200                      Trip always.           Biology        1

3. Muestra los nombres de los estudiantes junto con los nombres de los departamentos a los que pertenecen.

In [261]:
query = '''
SELECT name, dept_name from student;
'''
result = pd.read_sql_query(query, conn)
result

name         dept_name
0      Dawn Taylor           Biology
1      Wanda Black           Biology
2   Susan Robinson           Biology
3    Crystal Woods       Mathematics
4   Travis Sanchez  Computer Science
5   Zachary Knight           Biology
6    Jacob Pittman           Biology
7  Marcus Gonzalez           Biology
8   Robert Clayton       Mathematics
9      Rebecca Lin       Mathematics

4. Calcula el salario promedio de los instructores en el departamento de 'Computer Science'.

In [262]:
query = '''
SELECT avg(salary) from instructor
where instructor.dept_name = "Computer Science"
'''
result = pd.read_sql_query(query, conn)
result

avg(salary)
0     61737.16

5. Encuentra el número de estudiantes inscritos en cada departamento.

In [263]:
query = '''
SELECT distinct dept_name, count(dept_name) as count from student
group by student.dept_name;
'''
result = pd.read_sql_query(query, conn)
result

dept_name  count
0           Biology      6
1  Computer Science      1
2       Mathematics      3

6. Muestra los nombres de los estudiantes y los títulos de los cursos que están tomando este semestre.

In [270]:
query = '''
select name, title
from (select ID, title, semester
      from takes natural join course) natural join student
where semester = "Spring";
'''
result = pd.read_sql_query(query, conn)
result

Empty DataFrame
Columns: [name, title]
Index: []

7. Lista estudiantes que toman o han tomado clases en el edificio "ZL7101"

In [265]:
query = '''
select distinct *
from (select ID from (select course_id from section where section.building = "ZL7101") natural join takes) natural join student;
'''
result = pd.read_sql_query(query, conn)
result

ID            name    dept_name  tot_cred
0  06003     Wanda Black      Biology       132
1  28865  Zachary Knight      Biology        30
2  86970  Robert Clayton  Mathematics        49
3  99705   Jacob Pittman      Biology        26

8. Lista los cursos que tienen más estudiantes inscritos que el promedio de inscripciones de todos los cursos.

In [266]:
query = '''
select course_id, sec_id
from (select avg(c) as average, c as population, t.*
      from (select count(ID) as c, takes.*
            from takes
            group by course_id) as t)
where population > average;
'''
result = pd.read_sql_query(query, conn)
result

course_id sec_id
0   Uefz257     84

9. Encuentra los instructores que enseñan más de un curso, incluyendo los títulos de los cursos que enseñan.

In [267]:
query = '''
select ID, title
from (select count(course_id) as c, teaches.*
      from teaches
      group by ID) natural join course
where c > 1
'''
result = pd.read_sql_query(query, conn)
result

ID               title
0  57372  Answer experience.
1  92814        Trip always.

10. Entra datos para que la pregunta 6 no salga vacía.

In [292]:
# newSectionData = [('rjtj402', '42', 'Spring', 2025, 'ZL7101', '475', 'vwW')]
# conn.executemany('insert into section values (?, ?, ?, ?, ?, ?, ?)', newSectionData)

# newTakesData = [('81095', 'rjtj402', '42', 'Spring', 2025, 'D'), ('99705', 'rjtj402', '42', 'Spring', 2025, 'C')]
# conn.executemany('insert into takes values (?, ?, ?, ?, ?, ?)', newTakesData)

query = '''
select *
from (select ID, title, semester
      from takes natural join course) natural join student
where semester = "Spring";
'''
result = pd.read_sql_query(query, conn)
result

ID                    title semester           name    dept_name  \
0  81095  American history glass.   Spring  Crystal Woods  Mathematics   
1  99705  American history glass.   Spring  Jacob Pittman      Biology   

   tot_cred  
0        31  
1        26

In [40]:
query = "SELECT avg(salary) from instructor;"
result = pd.read_sql_query(query, conn)
result

avg(salary)
0    72304.284

In [41]:
# prompt: Lista todos los cursos con menos de 3 créditos.

query = """
SELECT title
FROM course
WHERE credits < 3;
"""
result = pd.read_sql_query(query, conn)
result


title
0                         Oil wall.
1                Answer experience.
2                  May stand guess.
3  Close certain national research.
4                      Trip always.